# [Chapter 10] Predicting sale price in Ames using LAD and LS

## [DSLC stages]: Analysis


The following code sets up the libraries and creates cleaned and pre-processed training, validation and test data that we will use in this document.

In [1]:
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
from sklearn.linear_model import LinearRegression, Ridge, Lasso
from sklearn.model_selection import cross_val_score, cross_validate
from sklearn.preprocessing import OneHotEncoder, scale, StandardScaler
import statsmodels.api as sm
from itertools import product
from joblib import Parallel, delayed

# define all of the objects we need
%run functions/prepare_ames_data.py


pd.set_option('display.max_columns', None)
pd.options.display.max_colwidth = 500
pd.options.display.max_rows = 100

## LS with multiple predictors

Since the `LinearRegression()` function from sklearn does not compute coefficient statistics, we will use the statsmodels package to fit the model using the OLS function instead.

In [2]:
y = ames_train_preprocessed['saleprice']
X_multi4 = ames_train_preprocessed[['gr_liv_area', 'year_built', 'overall_qual', 'bedroom_abvgr']]
X_multi4 = sm.add_constant(X_multi4)

ls_multi4 = sm.OLS(y, X_multi4).fit()


### Comparing coefficients

Comparing the coefficients using the *theoretical* $t$-values can be done by applying the `summary()` method to the `ls_multi4` object (look at the `t value` column): 


In [3]:
ls_multi4.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:              saleprice   R-squared:                       0.804
Model:                            OLS   Adj. R-squared:                  0.803
Method:                 Least Squares   F-statistic:                     1148.
Date:                Tue, 19 Dec 2023   Prob (F-statistic):               0.00
Time:                        19:14:45   Log-Likelihood:                -13248.
No. Observations:                1126   AIC:                         2.651e+04
Df Residuals:                    1121   BIC:                         2.653e+04
Df Model:                           4                                         
Covariance Type:            nonrobust                                         
=================================================================================
                    coef    std err          t      P>|t|      [0.025      0.975]
---------------------------------------------------------------------------------
const         -8.716e+05   7.09e+04    -12.296      0.000   -1.01e+06   -7.33e+05
gr_liv_area      87.6604      2.840     30.862      0.000      82.087      93.233
year_built      426.2441     37.118     11.483      0.000     353.415     499.074
overall_qual   1.913e+04   1042.247     18.354      0.000    1.71e+04    2.12e+04
bedroom_abvgr -1.267e+04   1455.145     -8.705      0.000   -1.55e+04   -9812.355
==============================================================================
Omnibus:                      412.324   Durbin-Watson:                   1.521
Prob(Omnibus):                  0.000   Jarque-Bera (JB):             4410.358
Skew:                           1.373   Prob(JB):                         0.00
Kurtosis:                      12.299   Cond. No.                     1.88e+05
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
[2] The condition number is large, 1.88e+05. This might indicate that there are
strong multicollinearity or other numerical problems.
"""


However, in veridical data science we prefer to empirically estimate the standard deviation of the coefficients in order to compute the t-values, where $t_j = b_j / SD(b_j)$, e.g., using the bootstrap. 

The following code uses the bootstrap (sampling with replacement) to create 1000 different perturbed versions of the data, computes a LS fit for each bootstrap sample, and reports the bootstrap coefficients in a nice tidy data frame (tibble):

In [4]:
# use the bootstrap (sampling with replacement) to create 1000 different perturbed versions of the data, computes a LS fit for each bootstrap sample, and reports the bootstrap coefficients in a nice tidy data frame

# define the number of bootstrap samples
n_bootstraps = 1000

# define the number of observations in the original dataset
n = ames_train_preprocessed.shape[0]

# create an empty list to store the bootstrap samples
bootstrap_samples = []

# create an empty list to store the bootstrap coefficients
bootstrap_coefs = []

# create a for loop to generate the bootstrap samples
for i in range(n_bootstraps):
    bootstrap_sample = ames_train_preprocessed.sample(n=n, replace=True)
    bootstrap_samples.append(bootstrap_sample)
    y_boot = bootstrap_sample['saleprice']
    X_multi4_boot = bootstrap_sample[['gr_liv_area', 'year_built', 'overall_qual', 'bedroom_abvgr']]
    X_multi4_boot = sm.add_constant(X_multi4_boot)
    ls_multi4_boot = sm.OLS(y_boot, X_multi4_boot).fit()
    bootstrap_coefs.append(ls_multi4_boot.params)

# convert the bootstrap coefficients into a data frame
bootstrap_coefs_df = pd.DataFrame(bootstrap_coefs)

bootstrap_coefs_df

const  gr_liv_area  year_built  overall_qual  bedroom_abvgr
0   -892868.647429    88.178966  436.493419  18582.566841  -11665.728461
1   -941699.904916    79.263297  461.771055  19287.004697   -9062.910894
2   -757406.112102    89.073258  367.966810  18252.063650  -11796.423235
3   -879374.769324    89.757915  428.348944  19387.569487  -12417.134929
4   -919463.371400    95.326054  450.279922  17943.769337  -14194.847099
..             ...          ...         ...           ...            ...
995 -840593.635732    84.142744  410.972116  19295.057999  -11901.873134
996 -824953.871620    88.159257  398.948133  20733.224744  -13314.791765
997 -872049.336730    79.526161  427.766487  19627.956804  -10539.929748
998 -796018.263337    81.640869  388.554189  19900.380561  -11349.840280
999 -882536.652773    92.073641  430.448237  18061.066878  -11871.934177

[1000 rows x 5 columns]


Then we can compute the standard deviation of each of the bootstrap coefficients, and use these standard deviation estimates to compute the standardized coefficients.

In [5]:
# compute the standard deviation of each of the bootstrap coefficients, 
# and use these standard deviation estimates to compute the standardized coefficients

# compute the standard deviation of each of the bootstrap coefficients
bootstrap_coefs_std = bootstrap_coefs_df.std(axis=0)

# compute the standardized coefficients
ls_multi4.summary2().tables[1]['Coef.'] / bootstrap_coefs_std

const           -11.844737
gr_liv_area      16.425664
year_built       10.972252
overall_qual     16.492928
bedroom_abvgr    -5.968054
dtype: float64

## Pre-processing: one-hot encoding

To create one-hot encoded binary (dummy) variables, you can either do it "manually" or you can use the `OneHotEncoder()` function from the sklearn.preprocessing library.

If the original "clean" (but not pre-processed) data looks like this:

In [6]:
ames_train_clean.head()

order  ms_subclass ms_zoning  lot_frontage  lot_area street alley  \
pid                                                                            
526351030    990           20        RL          87.0     11029   Pave   NaN   
526353050    991           20        RL           NaN     12925   Pave   NaN   
526354070    992           60        RL          85.0     11075   Pave   NaN   
527105050    993           60        RL          72.0      8702   Pave   NaN   
527106140    995           60        RL          59.0      9535   Pave   NaN   

          lot_shape land_contour utilities lot_config land_slope neighborhood  \
pid                                                                             
526351030       IR1          Lvl    AllPub     Corner        Gtl        NAmes   
526353050       IR1          Lvl    AllPub     Corner        Gtl        NAmes   
526354070       Reg          Lvl    AllPub     Inside        Gtl        NAmes   
527105050       IR1          Lvl    AllPub     Inside        Gtl      Gilbert   
527106140       IR1          Lvl    AllPub     Inside        Gtl      Gilbert   

          condition_1 condition_2 bldg_type house_style  overall_qual  \
pid                                                                     
526351030        Norm        Norm      1Fam      1Story             6   
526353050        Norm        Norm      1Fam      1Story             6   
526354070        Norm        Norm      1Fam      2Story             6   
527105050        Norm        Norm      1Fam      2Story             6   
527106140        Norm        Norm      1Fam      2Story             6   

           overall_cond  year_built  year_remod_add roof_style roof_matl  \
pid                                                                        
526351030             8        1958            2002        Hip   CompShg   
526353050             7        1970            1970      Gable   CompShg   
526354070             5        1969            1969      Gable   CompShg   
527105050             5        1997            1998      Gable   CompShg   
527106140             5        1998            1998      Gable   CompShg   

          exterior_1st exterior_2nd mas_vnr_type  mas_vnr_area exter_qual  \
pid                                                                         
526351030      MetalSd      MetalSd         None           0.0         Ex   
526353050      BrkFace      Plywood         None           0.0         TA   
526354070      HdBoard      HdBoard         None           0.0         TA   
527105050      VinylSd      VinylSd         None           0.0         TA   
527106140      VinylSd      VinylSd         None           0.0         TA   

          exter_cond foundation bsmt_qual bsmt_cond bsmt_exposure  \
pid                                                                 
526351030         TA     CBlock        Gd        TA            No   
526353050         TA     CBlock        TA        TA            Mn   
526354070         TA     CBlock        Fa        TA            Mn   
527105050         TA      PConc        TA        TA            No   
527106140         TA      PConc        Gd        TA            Gd   

          bsmtfin_type_1  bsmtfin_sf_1 bsmtfin_type_2  bsmtfin_sf_2  \
pid                                                                   
526351030            ALQ           528            BLQ           411   
526353050            BLQ           865            Unf             0   
526354070            ALQ           500            LwQ           276   
527105050            BLQ           706            Unf             0   
527106140            GLQ           851            Unf             0   

           bsmt_unf_sf  total_bsmt_sf heating heating_qc central_air  \
pid                                                                    
526351030          245           1184    GasA         Ex           Y   
526353050          340           1205    GasA         Ex           Y   
526354070          176     

Then the version with dummy variables for the specified columns looks like this (the binary dummy variable columns are placed at the end):

In [7]:
# extract the categorical variable names from ames_train_clean
cat_var_names = ames_train_clean.select_dtypes(include=['object']).columns
cat_var_names

Index(['ms_zoning', 'street', 'alley', 'lot_shape', 'land_contour',
       'utilities', 'lot_config', 'land_slope', 'neighborhood', 'condition_1',
       'condition_2', 'bldg_type', 'house_style', 'roof_style', 'roof_matl',
       'exterior_1st', 'exterior_2nd', 'mas_vnr_type', 'exter_qual',
       'exter_cond', 'foundation', 'bsmt_qual', 'bsmt_cond', 'bsmt_exposure',
       'bsmtfin_type_1', 'bsmtfin_type_2', 'heating', 'heating_qc',
       'central_air', 'electrical', 'kitchen_qual', 'functional',
       'fireplace_qu', 'garage_type', 'garage_finish', 'garage_qual',
       'garage_cond', 'paved_drive', 'pool_qc', 'fence', 'misc_feature',
       'sale_type'],
      dtype='object')

In [8]:
ames_train_clean_dummies = pd.get_dummies(
    ames_train_clean, 
    columns=cat_var_names,        
    drop_first=True
    )
ames_train_clean_dummies.head()

order  ms_subclass  lot_frontage  lot_area  overall_qual  \
pid                                                                   
526351030    990           20          87.0     11029             6   
526353050    991           20           NaN     12925             6   
526354070    992           60          85.0     11075             6   
527105050    993           60          72.0      8702             6   
527106140    995           60          59.0      9535             6   

           overall_cond  year_built  year_remod_add  mas_vnr_area  \
pid                                                                 
526351030             8        1958            2002           0.0   
526353050             7        1970            1970           0.0   
526354070             5        1969            1969           0.0   
527105050             5        1997            1998           0.0   
527106140             5        1998            1998           0.0   

           bsmtfin_sf_1  bsmtfin_sf_2  bsmt_unf_sf  total_bsmt_sf  1st_flr_sf  \
pid                                                                             
526351030           528           411          245           1184        1414   
526353050           865             0          340           1205        2117   
526354070           500           276          176            952        1092   
527105050           706             0          220            926         926   
527106140           851             0           75            926         926   

           2nd_flr_sf  low_qual_fin_sf  gr_liv_area  bsmt_full_bath  \
pid                                                                   
526351030           0                0         1414             1.0   
526353050           0                0         2117             0.0   
526354070        1020                0         2112             0.0   
527105050         678                0         1604             0.0   
527106140         678                0         1604             0.0   

           bsmt_half_bath  full_bath  half_bath  bedroom_abvgr  kitchen_abvgr  \
pid                                                                             
526351030             0.0          1          0              3              1   
526353050             0.0          2          1              4              1   
526354070             0.0          2          1              4              1   
527105050             0.0          2          1              3              1   
527106140             0.0          2          1              3              1   

           totrms_abvgrd  fireplaces  garage_yr_blt  garage_cars  garage_area  \
pid                                                                             
526351030              6           1           2002            2          601   
526353050              7           2           1970            2          550   
526354070              9           2           1969            2          576   
527105050              7           1           1998            2          470   
527106140              7           0           1998            2          472   

           wood_deck_sf  open_porch_sf  enclosed_porch  3ssn_porch  \
pid                                                                  
526351030             0             51               0           0   
526353050             0             42               0           0   
526354070           280              0               0           0   
527105050             0             36               0           0   
527106140           100             82               0           0   

           screen_porch  pool_area  misc_val  mo_sold  yr_sold  saleprice  \
pid                                                                         
526351030           190          0         0        5     2008     176500   
526353050             0          0         0        5     2008     237500   
526354070             0     



The `drop_first = True` argument specifies that the first level of the factor variable will be the reference level and no binary variable is created for it.

We included code for creating dummy variables in the `functions/preprocess_ames_data.py` file. (Some variables are manually converted to binary dummy variables, and others are converted using `pd.get_dummies()`.)



We could then include these dummy variables in a statsmodels `OLS()` fit or scikit.learn `linearRegression()` fit.

For example:


In [9]:
# extract the gr_liv_area, overall_qual, year_built, bedroom_abvgr, and neighborhood dummy columns from ames_train_clean_dummies
X_dummy = ames_train_clean_dummies[['gr_liv_area', 'year_built', 'overall_qual', 'bedroom_abvgr'] + list(ames_train_clean_dummies.filter(regex='neighborhood').columns)]
# fit the linear regression model with the dummy variables
ls_dummy_fit = LinearRegression()
ls_dummy_fit.fit(X=X_dummy,
                 y=ames_train_clean_dummies['saleprice'])
# print out the coefficients in a data frame
pd.DataFrame([ls_dummy_fit.intercept_] + [round(x, 2) for x in ls_dummy_fit.coef_],
             index=['intercept'] + list(X_dummy.columns),
                columns=['coefficients'])

coefficients
intercept            -597245.907818
gr_liv_area               77.890000
year_built               294.990000
overall_qual           16272.630000
bedroom_abvgr         -10253.400000
neighborhood_Blueste   -6236.650000
neighborhood_BrDale   -33286.590000
neighborhood_BrkSide    1768.420000
neighborhood_ClearCr   25646.010000
neighborhood_CollgCr   10628.490000
neighborhood_Crawfor   21831.730000
neighborhood_Edwards   -1807.800000
neighborhood_Gilbert   -4473.210000
neighborhood_Greens    -6540.070000
neighborhood_IDOTRR    -6432.050000
neighborhood_Landmrk  -23357.900000
neighborhood_MeadowV  -18452.100000
neighborhood_Mitchel   12832.020000
neighborhood_NAmes      8637.510000
neighborhood_NPkVill  -14903.730000
neighborhood_NWAmes     2826.370000
neighborhood_NoRidge   63752.350000
neighborhood_NridgHt   51242.650000
neighborhood_OldTown   -8421.530000
neighborhood_SWISU    -12869.240000
neighborhood_Sawyer    11951.880000
neighborhood_SawyerW      28.960000
neighborhood_Somerst    6396.830000
neighborhood_StoneBr   62012.070000
neighborhood_Timber    26613.870000
neighborhood_Veenker   40751.960000


## LS with all predictive features

The following code uses all (pre-processed) predictive features to compute a LS fit for sale price:

In [10]:
ls_all_fit = LinearRegression()
ls_all_fit.fit(X=ames_train_preprocessed.drop(columns=['saleprice']),
               y=ames_train_preprocessed['saleprice'])

pd.DataFrame([ls_all_fit.intercept_] + [round(x, 2) for x in ls_all_fit.coef_],
             index=['intercept'] + list(ames_train_preprocessed.drop(columns=['saleprice']).columns),
             columns=['coefficients'])

coefficients
intercept                -890816.220707
lot_frontage                 251.670000
lot_area                       0.360000
overall_qual               10820.980000
overall_cond                5665.480000
year_built                   221.920000
year_remod_add               -30.890000
mas_vnr_area                  55.090000
exter_qual                  6236.680000
bsmt_qual                  -1662.110000
bsmt_exposure               5398.340000
total_bsmt_sf                 22.000000
heating_qc                  2241.730000
gr_liv_area                   64.960000
bedroom_abvgr              -6033.970000
kitchen_qual                5666.750000
totrms_abvgrd               -912.030000
fireplaces                  4397.290000
fireplace_qu                -277.960000
garage_yr_blt                 52.980000
garage_finish               1658.180000
garage_cars                  -46.980000
garage_area                   20.150000
wood_deck_sf                   4.590000
mo_sold                      317.220000
yr_sold                      157.700000
masonry_veneer_brick      -11107.730000
foundation_cinder          -6861.650000
foundation_concrete         3294.530000
garage_attached            -3598.780000
lot_inside                  3312.090000
exterior_vinyl             -3220.640000
bathrooms                   3605.050000
porch                      -2345.960000
residential_density        -9770.040000
irregular_lot_shape         3307.560000
house_floors               -5895.610000
basement_finished_rating    1661.270000
neighborhood_BrkSide        4221.760000
neighborhood_CollgCr      -11102.610000
neighborhood_Edwards       -9877.070000
neighborhood_Gilbert       -9910.460000
neighborhood_Mitchel       -9123.830000
neighborhood_NAmes         -4823.370000
neighborhood_NWAmes       -12599.100000
neighborhood_OldTown       -7108.040000
neighborhood_Sawyer        -4841.010000
neighborhood_Somerst      -19785.860000


## Feature selection

Identifying which variables are highly correlated with the response can be done using the `corr()` function:

In [11]:
# compute the correlation between each feature with sale price
cor_sale_price = ames_train_preprocessed.corr()['saleprice'].sort_values(ascending=False).drop(index='saleprice')
cor_sale_price

overall_qual                0.775636
gr_liv_area                 0.774697
bathrooms                   0.667963
exter_qual                  0.628226
kitchen_qual                0.623952
total_bsmt_sf               0.614326
garage_cars                 0.608155
garage_area                 0.597452
totrms_abvgrd               0.531032
bsmt_qual                   0.527913
mas_vnr_area                0.526472
fireplace_qu                0.505738
garage_finish               0.500433
fireplaces                  0.484057
year_built                  0.481019
year_remod_add              0.475411
foundation_concrete         0.459448
garage_yr_blt               0.451576
garage_attached             0.430963
heating_qc                  0.397898
bsmt_exposure               0.394690
lot_frontage                0.363656
wood_deck_sf                0.343653
masonry_veneer_brick        0.334052
basement_finished_rating    0.311100
irregular_lot_shape         0.305052
exterior_vinyl              0.297013
l


We can count how many are greater than 0.5:

In [12]:
high_cor = cor_sale_price[cor_sale_price >= 0.5]
high_cor

overall_qual     0.775636
gr_liv_area      0.774697
bathrooms        0.667963
exter_qual       0.628226
kitchen_qual     0.623952
total_bsmt_sf    0.614326
garage_cars      0.608155
garage_area      0.597452
totrms_abvgrd    0.531032
bsmt_qual        0.527913
mas_vnr_area     0.526472
fireplace_qu     0.505738
garage_finish    0.500433
Name: saleprice, dtype: float64

Which shows that 13 of the correlations are greater than (or equal to) 0.5.

You could train a LS fit just using these features as follows:

In [13]:
ls_cor_fit = LinearRegression()
ls_cor_fit.fit(X=ames_train_preprocessed.filter(high_cor.index),
               y=ames_train_preprocessed['saleprice'])
pd.DataFrame([ls_cor_fit.intercept_] + [round(x, 2) for x in ls_cor_fit.coef_],
             index=['intercept'] + list(ames_train_preprocessed.filter(high_cor.index).columns),
             columns=['coefficients'])

coefficients
intercept     -96674.557565
overall_qual   11367.660000
gr_liv_area       59.920000
bathrooms       8074.960000
exter_qual      7994.850000
kitchen_qual   12794.640000
total_bsmt_sf     33.620000
garage_cars    -1539.020000
garage_area       32.610000
totrms_abvgrd  -4548.000000
bsmt_qual       -896.470000
mas_vnr_area      45.030000
fireplace_qu    1721.570000
garage_finish   3482.220000


## Ridge and lasso

### Choosing $\lambda$ using cross-validation

Using 10-fold cross-validation to choose the ridge hyperparameter can be done using the `cross_validate()` function from the scikit.learn library.

**Note that the `alpha` parameter used in the Lasso and Ridge functions from scikit learn are different from the lambda parameter used in the glmnet function in R, so our resulting plots look somewhat different.**




In [14]:
X = ames_train_preprocessed.drop(columns=['saleprice'])
# scale the predictors
X_std = (X - X.mean()) / X.std()
y = ames_train_preprocessed['saleprice']

In [15]:
# use 10-fold cross-validation to select the best lambda (alpha) value for the ridge regression model

# define the alpha values to test
# note that the start/stop values in the first two arguments are the exponents
alphas = np.logspace(-1, 6, 100)

# create an empty list to store the cross-validation scores
ridge_cv_scores = []

# create a for loop to compute the cross-validation score for each alpha value
for alpha in alphas:
    ridge = Ridge(alpha=alpha)
    ridge_cv = cross_validate(estimator=ridge,
                              X=X_std,
                              y=y,
                              cv=10,
                              scoring='neg_root_mean_squared_error')
    ridge_cv_scores.append({'alpha': alpha,
                            'log_alpha': np.log(alpha),
                            'test_mse': -np.mean(ridge_cv['test_score'])})

# convert the cross-validation scores into a data frame
ridge_cv_scores_df = pd.DataFrame(ridge_cv_scores)

# plot the cross-validation scores as a function of alpha
px.line(ridge_cv_scores_df,
        x='log_alpha',
        y='test_mse',
        title='Ridge')

In [16]:
# use 10-fold cross-validation to select the best lambda (alpha) value for the lasso regression model

# define the alpha values to test
# note that the start/stop values in the first two arguments are the exponents
alphas = np.logspace(-1, 4, 100)

# create an empty list to store the cross-validation scores
lasso_cv_scores = []

# create a for loop to compute the cross-validation score for each alpha value
for alpha in alphas:
    lasso = Lasso(alpha=alpha)
    lasso_cv = cross_validate(estimator=lasso,
                              X=X_std,
                              y=y,
                              cv=10,
                              scoring='neg_root_mean_squared_error')
    lasso_cv_scores.append({'alpha': alpha,
                            'log_alpha': np.log(alpha),
                            'test_mse': -np.mean(lasso_cv['test_score'])})

# convert the cross-validation scores into a data frame
lasso_cv_scores_df = pd.DataFrame(lasso_cv_scores)

# plot the cross-validation scores as a function of alpha
px.line(lasso_cv_scores_df,
        x='log_alpha',
        y='test_mse',
        title='Lasso')



### Fitting ridge and lasso models

Let's extract the "best" alpha values for each fit:

In [17]:

# identify the value of alpha that minimizes the cross-validation score for ridge
ridge_alpha_min = ridge_cv_scores_df.sort_values(by='test_mse').head(1).alpha.values[0]
# compute the min MSE and the SE of the MSE
mse_se_ridge = ridge_cv_scores_df['test_mse'].std() / np.sqrt(10)
mse_min_ridge = ridge_cv_scores_df['test_mse'].min()


# identify the value of alpha that minimizes the cross-validation score for ridge within 1SE
ridge_alpha_1se = ridge_cv_scores_df[(ridge_cv_scores_df['test_mse'] <= mse_min_ridge + mse_se_ridge) & 
                                     (ridge_cv_scores_df['test_mse'] >= mse_min_ridge - mse_se_ridge)].sort_values(by='alpha', ascending=False).head(1).alpha.values[0]


# identify the value of alpha that minimizes the cross-validation score for lasso
lasso_alpha_min = lasso_cv_scores_df.sort_values(by='test_mse').head(1).alpha.values[0]
# compute the min MSE and the SE of the MSE
mse_se_lasso = lasso_cv_scores_df['test_mse'].std() / np.sqrt(10)
mse_min_lasso = lasso_cv_scores_df['test_mse'].min()

# identify the value of alpha that minimizes the cross-validation score for lasso within 1SE
lasso_alpha_1se = lasso_cv_scores_df[(lasso_cv_scores_df['test_mse'] <= mse_min_lasso + mse_se_lasso) & 
                                     (lasso_cv_scores_df['test_mse'] >= mse_min_lasso - mse_se_lasso)].sort_values(by='alpha', ascending=False).head(1).alpha.values[0]


In [18]:
print('Ridge (min): ', ridge_alpha_min)
print('Ridge (1SE): ', ridge_alpha_1se)
print('Lasso (min): ', lasso_alpha_min)
print('Lasso (1SE): ', lasso_alpha_1se)

Ridge (min):  35.11191734215131
Ridge (1SE):  1747.5284000076829
Lasso (min):  191.79102616724887
Lasso (1SE):  1097.4987654930567


Having chosen the `alpha` values for ridge and lasso using CV, we can fit the ridge and lasso models.

In [19]:
# use ridge_alpha_min to fit the ridge regression model
ridge_min_fit = Ridge(alpha=ridge_alpha_min).fit(X=X_std, y=y)
ridge_1se_fit = Ridge(alpha=ridge_alpha_1se).fit(X=X_std, y=y)

# use lasso_alpha_min to fit the lasso regression model
lasso_min_fit = Lasso(alpha=lasso_alpha_min).fit(X=X_std, y=y)
lasso_1se_fit = Lasso(alpha=lasso_alpha_1se).fit(X=X_std, y=y)



### Exploring coefficient shrinkage

Let's visualize how much each regularization algorithm shrinks each coefficient.

To do that, we need to extract the coefficients from each regularized fit, as well as the original fit with all features. 

First, we will re-compute the original fit using standardized variables so that the coefficients are comparable to the ridge and lasso coefficients):

In [20]:
# compute the LS model using linearregression (X has been standardized above)
ls_std = LinearRegression()
ls_std.fit(X=X_std, y=y)

# extract the coefficients from the LS model
ls_std_coefs = pd.DataFrame([round(abs(x), 2) for x in ls_std.coef_],
                            index=list(ames_train_preprocessed.drop(columns=['saleprice']).columns),
                            columns=['ls'])

Then we can extract the coefficients from each of the regularized fits

In [21]:
# extract the coefficients from the lasso and ridge models
ridge_min_coefs = pd.DataFrame([round(abs(x), 2) for x in ridge_min_fit.coef_],
                           index=list(ames_train_preprocessed.drop(columns=['saleprice']).columns),
                           columns=['ridge_min'])
ridge_1se_coefs = pd.DataFrame([round(abs(x), 2) for x in ridge_1se_fit.coef_],
                           index=list(ames_train_preprocessed.drop(columns=['saleprice']).columns),
                           columns=['ridge_1se'])
lasso_min_coefs = pd.DataFrame([round(abs(x), 2) for x in lasso_min_fit.coef_],
                            index=list(ames_train_preprocessed.drop(columns=['saleprice']).columns),
                            columns=['lasso_min'])
lasso_1se_coefs = pd.DataFrame([round(abs(x), 2) for x in lasso_1se_fit.coef_],
                            index=list(ames_train_preprocessed.drop(columns=['saleprice']).columns),
                            columns=['lasso_1se'])


In [22]:
# compute the order of the coeffiicnets in terms of absolute value
ls_std_coefs = ls_std_coefs.sort_values(by='ls', ascending=False)
# merge the coefficients into a single data frame
coefs = ls_std_coefs.merge(ridge_min_coefs, left_index=True, right_index=True)
coefs = coefs.merge(lasso_min_coefs, left_index=True, right_index=True) \
             .merge(ridge_1se_coefs, left_index=True, right_index=True) \
             .merge(lasso_1se_coefs, left_index=True, right_index=True)
# convert to long form 
coefs = coefs.reset_index().melt(id_vars='index', var_name='model', value_name='coefficients')
coefs = coefs.rename(columns={'index': 'variable'})

# place the LS coefficients in its own column and remove the original rows with LS coefficients
coefs["ls_coefficients"] = list(coefs.query('model == "ls"').coefficients) * 5
coefs = coefs.query('model != "ls"')


Then can create a plot that compares the unregularized and regularized coefficients for each regularized fit.

The figure below shows that the lasso fit with $\lambda_{min}$ implemented almost no shrinkage (implying that this regularization parameter was not large enough to actually perform any meaningful regularization). The ridge fit with $\lambda_{min}$ involves slightly more regularization than the corresponding lasso fit with $\lambda_{min}$, but most of the coeﬀicients are still very similar to their unregularized counterparts. 

In [23]:
fig = px.scatter(x='variable', 
                 y='ls_coefficients', 
                 labels=dict(variable='Variable', ls_coefficients='Coefficients'),
                 data_frame=coefs, 
                 facet_row='model',
                 color_discrete_sequence=['rgb(128,128,128)'],
                 height=900)

# add just the ls_coefficients values to each facet in fig
i = 5
for model_var in coefs.model.unique():
    fig.add_trace(go.Scatter(x=coefs.query('model == @model_var').variable,
                             y=coefs.query('model == @model_var').coefficients,
                             mode='markers+lines',
                             line=dict(color='black'),
                             showlegend=False),
                  row=i-1, col=1)
    i-=1

fig


## PCS evaluations

### Predictability

Let's compare the performance of each fit on the validation set houses. 


Before we get started, we need to create a matrix version of the validation set for fitting ridge and lasso. However, note that we will use the mean and SD from the training set to standardize the validation set (the logic here is that if we were using these algorithm to predict the response of a new data point, we would use the training data mean and SD to standardize it).


In [24]:
X_train = ames_train_preprocessed.drop(columns=['saleprice'])
X_val = ames_val_preprocessed.drop(columns=['saleprice'])

# standardize the training and validation sets using the mean and SD from the training data
ames_train_preprocessed_std = (ames_train_preprocessed - ames_train_preprocessed.mean()) / ames_train_preprocessed.std()
ames_val_preprocessed_std = (ames_val_preprocessed - ames_train_preprocessed.mean()) / ames_train_preprocessed.std()
# extract the predictors and response from the standardized training and validation sets
X_train_std = ames_train_preprocessed_std.drop(columns=['saleprice'])
y_val_std = ames_val_preprocessed_std['saleprice']
X_val_std = ames_val_preprocessed_std.drop(columns=['saleprice']) 

Let's compute predictions for each fit (ls_area_fit, ls_multi_fit, ls_all_fit, ridge_1se_fit, lasso_1se_fit). Let's re-define the basic LS fits using the standardized data we just defined

In [25]:
ls_area_fit = LinearRegression()
ls_area_fit.fit(X=np.array(X_train_std['gr_liv_area']).reshape(-1, 1),
                y=ames_train_preprocessed['saleprice'])
ls_multi_fit = LinearRegression()
ls_multi_fit.fit(X=X_train_std[['gr_liv_area', 'year_built', 'overall_qual', 'bedroom_abvgr'] + list(X_val_std.filter(regex='neighborhood').columns)],
                 y=ames_train_preprocessed['saleprice'])
ls_all_fit = LinearRegression()
ls_all_fit.fit(X=X_train_std,
               y=ames_train_preprocessed['saleprice'])

LinearRegression()

In [26]:
# compute the predictions on the validaion set for ls_area_fit, ls_multi_fit, ls_all_fit, ridge_1se_fit, and lasso_1se_fit
ls_area_val_pred = ls_area_fit.predict(X=np.array(X_val_std['gr_liv_area']).reshape(-1, 1))
ls_multi_val_pred = ls_multi_fit.predict(X=X_val_std[['gr_liv_area', 'year_built', 'overall_qual', 'bedroom_abvgr'] + list(X_val_std.filter(regex='neighborhood').columns)])
ls_all_val_pred = ls_all_fit.predict(X=X_val_std)
ridge_1se_val_pred = ridge_1se_fit.predict(X=X_val_std)
lasso_1se_val_pred = lasso_1se_fit.predict(X=X_val_std)

In [27]:
# evaluate the rMSE, MAE and correlation of each fit
# create an empty list to store the results
val_results = []
# compute the rMSE, MAE and correlation for each fit
val_results.append({'model': 'ls_area',
                    'rmse': np.sqrt(np.mean((ames_val_preprocessed['saleprice'] - ls_area_val_pred)**2)),
                    'mae': np.mean(abs(ames_val_preprocessed['saleprice'] - ls_area_val_pred)),
                    'corr': np.corrcoef(ames_val_preprocessed['saleprice'], ls_area_val_pred)[0, 1]})
val_results.append({'model': 'ls_multi',
                    'rmse': np.sqrt(np.mean((ames_val_preprocessed['saleprice'] - ls_multi_val_pred)**2)),
                    'mae': np.mean(abs(ames_val_preprocessed['saleprice'] - ls_multi_val_pred)),
                    'corr': np.corrcoef(ames_val_preprocessed['saleprice'], ls_multi_val_pred)[0, 1]})
val_results.append({'model': 'ls_all',
                    'rmse': np.sqrt(np.mean((ames_val_preprocessed['saleprice'] - ls_all_val_pred)**2)),
                    'mae': np.mean(abs(ames_val_preprocessed['saleprice'] - ls_all_val_pred)),
                    'corr': np.corrcoef(ames_val_preprocessed['saleprice'], ls_all_val_pred)[0, 1]})
val_results.append({'model': 'ridge_1se',
                    'rmse': np.sqrt(np.mean((ames_val_preprocessed['saleprice'] - ridge_1se_val_pred)**2)),
                    'mae': np.mean(abs(ames_val_preprocessed['saleprice'] - ridge_1se_val_pred)),
                    'corr': np.corrcoef(ames_val_preprocessed['saleprice'], ridge_1se_val_pred)[0, 1]})
val_results.append({'model': 'lasso_1se',
                    'rmse': np.sqrt(np.mean((ames_val_preprocessed['saleprice'] - lasso_1se_val_pred)**2)),
                    'mae': np.mean(abs(ames_val_preprocessed['saleprice'] - lasso_1se_val_pred)),
                    'corr': np.corrcoef(ames_val_preprocessed['saleprice'], lasso_1se_val_pred)[0, 1]})
# convert the results into a data frame
val_results_df = pd.DataFrame(val_results)
val_results_df

model          rmse           mae      corr
0    ls_area  49376.502965  34713.526132  0.696312
1   ls_multi  31773.395693  23857.936133  0.886903
2     ls_all  23250.505397  17311.648732  0.942223
3  ridge_1se  26176.076500  17876.480367  0.932649
4  lasso_1se  23048.818263  16657.436120  0.942280

Note that the three fits with all of the predictors (`ls_all`, `ridge_fit`, and `lasso_fit`) all have fairly similar (and fairly good, in terms of correlation) predictive performance. 


### Stability


#### Stability to data perturbations


To assess the stability of our data to appropriate perturbations in the data, we first need to decide what makes an "appropriate" perturbation. That is, what type of data perturbation (e.g., adding random noise, or performing sampling) most resembles the way that the data *could* have been measured or collected differently, as well as how these results will be applied in the future. 


While the Ames housing data does not correspond to a random sample from a greater population of houses, each house is more-or-less exchangeable, meaning that a random sampling technique would be a reasonable perturbation, so we will draw 100 bootstrap samples of the original data. 

Moreover, it is plausible that the living area measurements involve a slight amount of measurement error, although we do not have a realistic sense of how much. To really stress-test our results, we choose to add another perturbation to the data that involves adding some random noise to 30% of the `gr_liv_area` measurements. Since the standard deviation of the living area is approximately 500, we decide to add or subtract a random number between 0 and 250 (i.e. add noise up to half a standard deviation) to 30% of `gr_liv_area` observations.

Since we will be repeating this analysis many times, we will write a function that will take an Ames dataset, and return a perturbed version of it.

In [28]:
# write a function that takes the ames_train_preprocessed data frame and creates a bootstrap sample of the same size
# and perturbs the gr_liv_area column by adding a random number between -250 and 250 to 30% of the values
def perturb_ames(df):
    # create a copy of the data frame
    df_copy = df.copy()
    # generate a random number between -250 and 250 for 30% of the rows
    sampled_index = df_copy.sample(frac=0.3).index
    df_copy.loc[sampled_index, 'gr_liv_area'] = df_copy.loc[sampled_index, 'gr_liv_area'] + np.random.randint(-250, 250, size=sampled_index.size)
    # conduct bootstrap sample
    df_copy = df_copy.sample(frac=1, replace=True)
    return df_copy

Below we create a list containing the 100 perturbed versions of the training data. 

In [29]:
# create a list of 100 perturbed versions of ames_train_preprocessed using the perturb_ames function
perturbed_ames = [perturb_ames(ames_train_preprocessed) for i in range(100)]

Then we can apply each fit to each of the 100 perturbed training datasets

In [30]:
def fit_models(df, reg=True, fit_area_multi=True):
    if fit_area_multi==True:
        ls_area = LinearRegression().fit(X=np.array(df['gr_liv_area']).reshape(-1, 1), y=df['saleprice'])
        ls_multi = LinearRegression().fit(X=df[['gr_liv_area', 'year_built', 'overall_qual', 'bedroom_abvgr'] + list(df.filter(regex='neighborhood').columns)],
                                                 y=df['saleprice'])
    
    ls_all = LinearRegression().fit(X=df.drop(columns='saleprice'),
                                    y=df['saleprice'])
    
    # if including the regularized fits, compute them
    if reg:
        
        # standardize predictor variables in df for ridge and lasso
        df_x = df.drop(columns='saleprice')
        df_x_std = (df_x - df_x.mean()) / df_x.std()
        df_y = df['saleprice']
        
        alphas = np.logspace(-1, 5, 100)
        ridge_cv_scores = []
        for alpha in alphas:
            ridge = Ridge(alpha=alpha)
            ridge_cv = cross_validate(estimator=ridge,
                                    X=df_x_std,
                                    y=df_y,
                                    cv=10,
                                    scoring='neg_root_mean_squared_error')
            ridge_cv_scores.append({'alpha': alpha,
                                    'log_alpha': np.log(alpha),
                                    'test_mse': -np.mean(ridge_cv['test_score'])})
            
        ridge_cv_scores_df = pd.DataFrame(ridge_cv_scores)
        ridge_alpha_min = ridge_cv_scores_df.sort_values(by='test_mse').head(1).alpha.values[0]
        # identify the 1SE value
        mse_se_ridge = ridge_cv_scores_df['test_mse'].std() / np.sqrt(10)
        mse_min_ridge = ridge_cv_scores_df['test_mse'].min()
        ridge_alpha_1se = ridge_cv_scores_df[(ridge_cv_scores_df['test_mse'] <= mse_min_ridge + mse_se_ridge) & 
                                            (ridge_cv_scores_df['test_mse'] >= mse_min_ridge - mse_se_ridge)].sort_values(by='alpha', ascending=False).head(1).alpha.values[0]
        ridge = Ridge(alpha=ridge_alpha_1se).fit(X=df_x_std, y=df_y)
        
        alphas = np.logspace(-2, 7, 100)
        lasso_cv_scores = []
        for alpha in alphas:
            lasso = Lasso(alpha=alpha)
            lasso_cv = cross_validate(estimator=lasso,
                                    X=df_x_std,
                                    y=df_y,
                                    cv=10,
                                    scoring='neg_root_mean_squared_error')
            lasso_cv_scores.append({'alpha': alpha,
                                    'log_alpha': np.log(alpha),
                                    'test_mse': -np.mean(lasso_cv['test_score'])})
        lasso_cv_scores_df = pd.DataFrame(lasso_cv_scores)
        lasso_alpha_min = lasso_cv_scores_df.sort_values(by='test_mse').head(1).alpha.values[0]
        # identify the 1SE value
        mse_se_lasso = lasso_cv_scores_df['test_mse'].std() / np.sqrt(10)
        mse_min_lasso = lasso_cv_scores_df['test_mse'].min()
        lasso_alpha_1se = lasso_cv_scores_df[(lasso_cv_scores_df['test_mse'] <= mse_min_lasso + mse_se_lasso) & 
                                            (lasso_cv_scores_df['test_mse'] >= mse_min_lasso - mse_se_lasso)].sort_values(by='alpha', ascending=False).head(1).alpha.values[0]
        lasso = Lasso(alpha=lasso_alpha_1se).fit(X=df_x_std, y=df_y)
        
        if fit_area_multi==True:
            return (ls_area, ls_multi, ls_all, ridge, lasso)    
        else:
            return (ls_all, ridge, lasso)
    
    elif fit_area_multi==True:
        return (ls_area, ls_multi, ls_all)
    
    else:
        return ls_all

In [31]:
# This code takes a while to run, so we will use the joblib library to parallelize the code
# compute the fits for each perturbed dataset
results = Parallel(n_jobs=-1)(delayed(fit_models)(df) for df in perturbed_ames)
ls_area_perturbed, ls_multi_perturbed, ls_all_perturbed, ridge_perturbed, lasso_perturbed = zip(*results)


In [32]:
# compute the predictions on the validaion set for ls_area_perturbed, ls_multi_perturbed, ls_all_perturbed, ridge_perturbed, and lasso_perturbed
ls_area_val_pred_perturbed = [ls_area_perturbed[i].predict(X=np.array(X_val['gr_liv_area']).reshape(-1, 1)) for i in range(100)]
ls_multi_val_pred_perturbed = [ls_multi_perturbed[i].predict(X=X_val[['gr_liv_area', 'year_built', 'overall_qual', 'bedroom_abvgr'] + list(X_val.filter(regex='neighborhood').columns)]) for i in range(100)]
ls_all_val_pred_perturbed = [ls_all_perturbed[i].predict(X=X_val) for i in range(100)]
ridge_val_pred_perturbed = [ridge_perturbed[i].predict(X=X_val_std) for i in range(100)]
lasso_val_pred_perturbed = [lasso_perturbed[i].predict(X=X_val_std) for i in range(100)]

Let's define a prediction stability plot function

In [33]:
# define a function that takes a list of predictions from ls_perturbed_pred and creates line segment plots for the 
# range of predictions for each id corresponding to the position in each list entry

def plot_prediction_range(pred_list, title=None, sample_index=None):
    if sample_index is None:
        sample_index = list(range(pred_list[0].size))
        
    pred_list = [pred_list[i][sample_index] for i in range(100)]
    pred_list_df = pd.DataFrame(pred_list).T
    pred_list_df['id'] = ames_val_preprocessed.index[sample_index]
    pred_list_df['true'] = ames_val_preprocessed['saleprice'].values[sample_index]
    pred_list_df = pd.melt(pred_list_df, id_vars=['id','true'], var_name='iter', value_name='pred')
    pred_list_df = pred_list_df.groupby(['id', 'true']).agg({'pred': ['min', 'max']})
    pred_list_df = pred_list_df.reset_index()
    pred_list_df = pred_list_df.set_index('id')

    # plot a series of horizontal line segments for each id where the lines range from the minimum and maximum predicted values on the x-axis and have the true value on the y-axis
    fig = go.Figure()

    for i in pred_list_df.index:
        fig.add_trace(
            go.Scatter(x=[pred_list_df.loc[i, ('pred', 'min')], pred_list_df.loc[i, ('pred', 'max')]],
                        y=[pred_list_df.loc[i, 'true'].values[0], pred_list_df.loc[i, 'true'].values[0]],
                        mode='lines',
                        line={'color': 'black'}, 
                        showlegend=False)
            )
    # add a single diagonal line to the plot
    fig.add_trace(
        go.Scatter(x=[0, 400000], y=[0, 400000], mode='lines', line={'color': 'black'}, showlegend=False)
    )
        
    fig.update_layout(xaxis_title='Predicted sale price range',
                        yaxis_title='Observed sale price',
                        title=title)
    return fig

And use it to visualize the range of perturbed predictions for 150 validation set houses for each fit. 

In [34]:
val_sample_id = np.random.choice(ames_val_preprocessed.shape[0], 150, replace=False)
plot_prediction_range(ls_area_val_pred_perturbed, 'LS (area only)', sample_index=val_sample_id)

In [35]:
plot_prediction_range(ls_multi_val_pred_perturbed, 'LS (multi)', sample_index=val_sample_id)

In [36]:
plot_prediction_range(ls_all_val_pred_perturbed, 'LS (all)', sample_index=val_sample_id)

In [37]:
plot_prediction_range(ridge_val_pred_perturbed, 'Ridge (1SE)', sample_index=val_sample_id)

In [38]:
plot_prediction_range(lasso_val_pred_perturbed, 'Lasso (1SE)', sample_index=val_sample_id)


It is clear that the range of predictions gets wider for the most complex fits with more predictive features (even though they are more accurate overall), but it looks like regularization helps increase the stability of these predictions slightly. 


Let's quantify the average sd of the predictions for each of the fits

In [39]:
print(f"LS (area only) average sd: {pd.DataFrame(ls_area_val_pred_perturbed).std(axis=0).mean()}")
print(f"LS (multi) average sd: {pd.DataFrame(ls_multi_val_pred_perturbed).std(axis=0).mean()}")
print(f"LS (all) average sd: {pd.DataFrame(ls_all_val_pred_perturbed).std(axis=0).mean()}")
print(f"Ridge (1SE) average sd: {pd.DataFrame(ridge_val_pred_perturbed).std(axis=0).mean()}")
print(f"Lasso (1SE) average sd: {pd.DataFrame(lasso_val_pred_perturbed).std(axis=0).mean()}")


LS (area only) average sd: 2337.640363477107
LS (multi) average sd: 3506.897060267339
LS (all) average sd: 5759.738977237314
Ridge (1SE) average sd: 4107.912081245528
Lasso (1SE) average sd: 4395.3841119662975



Lastly, we will look at the stability of the coefficients themselves.

Let's aggregate the coefficients for each fit together. However, to ensure that the ridge/lasso coefficients are comparable with the unregularized coefficients, we will re-fit each of the unregularized fits using the standardized data.

In [40]:
# create perturbations of the standardized dataset
perturbed_ames_std = [df.drop(columns='saleprice') for df in perturbed_ames]
perturbed_ames_std = [(df - df.mean()) / df.std() for df in perturbed_ames_std]
# add sale price back to each perturbed data frame
perturbed_ames_std = [df.merge(ames_train_preprocessed['saleprice'], left_index=True, right_index=True) for df in perturbed_ames_std]

# refit all of the unregularized fits
results_std = Parallel(n_jobs=-1)(delayed(fit_models)(df, reg=False) for df in perturbed_ames_std)
ls_area_perturbed_std, ls_multi_perturbed_std, ls_all_perturbed_std = zip(*results_std)

In [41]:
def extract_coefficients(fit_perturbed_list, model=None):
    coefs_list = []
    for i in range(100):
        # The single-predictor fit doesn't provide variable names, so we need to manually provide this
        if fit_perturbed_list[0].coef_.shape[0] == 1:
            var_names = 'gr_liv_area'
        else: 
            var_names = fit_perturbed_list[i].feature_names_in_
        
        coefs = pd.DataFrame({'variable': var_names,
                              'coef': fit_perturbed_list[i].coef_,
                              'model': model})
        coefs['iter'] = i
        coefs_list.append(coefs)
    coefs_combined_df = pd.concat(coefs_list)
    return coefs_combined_df


In [42]:
# extract coefficients for all models
perturbed_std_coefs_ls_area = extract_coefficients(ls_area_perturbed_std, 'ls_area')
perturbed_std_coefs_ls_multi = extract_coefficients(ls_multi_perturbed_std, 'ls_multi')
perturbed_std_coefs_ls_all = extract_coefficients(ls_all_perturbed_std, 'ls_all')
perturbed_std_coefs_ridge = extract_coefficients(ridge_perturbed, 'ridge')
perturbed_std_coefs_lasso = extract_coefficients(lasso_perturbed, 'lasso')

# concatenate the dataframes
perturbed_std_coefs_combined = pd.concat([perturbed_std_coefs_ls_area, 
                                     perturbed_std_coefs_ls_multi, 
                                     perturbed_std_coefs_ls_all, 
                                     perturbed_std_coefs_ridge, 
                                     perturbed_std_coefs_lasso])



Then we can visualize the top 20 coefficients (based on the LS (all predictors) fit)

In [43]:
# identify the 20 variables with the largest coefficients in the LS (all) model
top_20_coefs_ls_all = perturbed_std_coefs_ls_all.groupby('variable') \
    .agg({'coef': 'mean'}) \
    .sort_values(by='coef', ascending=False) \
    .head(20) \
    .index
top_20_coefs_ls_all

Index(['gr_liv_area', 'overall_qual', 'mas_vnr_area', 'total_bsmt_sf',
       'overall_cond', 'year_built', 'bsmt_exposure', 'lot_frontage',
       'garage_area', 'kitchen_qual', 'bathrooms', 'exter_qual',
       'basement_finished_rating', 'lot_area', 'fireplaces', 'garage_yr_blt',
       'heating_qc', 'irregular_lot_shape', 'foundation_concrete',
       'garage_finish'],
      dtype='object', name='variable')

Then we can create a series of boxplots showing the distribution of each perturbed coefficient for each fit

In [44]:
# extract the coefficients for the top 20 variables from perturbed_std_coefs_combined and visualize their distributions using boxplots
top_20_coefs_df = perturbed_std_coefs_combined.query('variable in @top_20_coefs_ls_all')

fig = px.box(top_20_coefs_df,
             x='variable',
             y='coef',
             facet_col='model',
             facet_col_wrap=1,
             height=1200,
             category_orders={'variable': top_20_coefs_ls_all})
fig.update_traces(width=0.5)
fig



#### Stability to cleaning/pre-processing judgment call perturbations


Next, we need to repeat this stability analysis, but instead of using data perturbations based on sampling and adding random noise, we will investigate perturbations to our cleaning and pre-processing judgment calls. 

First, we need to identify all of the judgment calls that we plan to perturb. The judgment calls (and the options) that we will consider are:


- `max_identical_thresh`: Missing value threshold of 0.65, 0.8, or 0.95 (i.e., we remove variables whose proportion of missing values exceeds this value).

- `n_neighborhoods`: Keeping the 10 or 20 largest neighborhoods (and aggregate the rest before computing neighborhood dummy variables).

- `impute_missing_categorical`: Impute missing categorical values with either an "other" value or the mode.

- `simplify_vars`: Simplify several variables (such as bathrooms, porch, etc) or not.

- `transform_response`: Apply a log or square-root transformation to the response, or leave it untransformed.

- `cor_feature_selection_threshold`: Apply correlation feature selection with a threshold of 0.5, or not applying correlation feature selection (threshold of 0).

- `convert_categorical`: Convert categorical variables directly to a numeric variable or create (simplified) dummy variables.


Let's create a data frame where each row corresponds to a unique combination of these judgment call options:



In [45]:
perturb_options = list(product([0.65, 0.8, 0.95], 
                               [10, 20],
                               ['other', 'mode'],
                               [True, False],
                               ['none', 'log', 'sqrt'],
                               [0, 0.5],
                               ['numeric', 'simplified_dummy', 'dummy']))
perturb_options = pd.DataFrame(perturb_options, columns=('max_identical_thresh', 
                                                         'n_neighborhoods',
                                                         'impute_missing_categorical',
                                                         'simplify_vars',
                                                         'transform_response',
                                                         'cor_feature_selection_threshold',
                                                         'convert_categorical'))
perturb_options

max_identical_thresh  n_neighborhoods impute_missing_categorical  \
0                    0.65               10                      other   
1                    0.65               10                      other   
2                    0.65               10                      other   
3                    0.65               10                      other   
4                    0.65               10                      other   
..                    ...              ...                        ...   
427                  0.95               20                       mode   
428                  0.95               20                       mode   
429                  0.95               20                       mode   
430                  0.95               20                       mode   
431                  0.95               20                       mode   

     simplify_vars transform_response  cor_feature_selection_threshold  \
0             True               none                              0.0   
1             True               none                              0.0   
2             True               none                              0.0   
3             True               none                              0.5   
4             True               none                              0.5   
..             ...                ...                              ...   
427          False               sqrt                              0.0   
428          False               sqrt                              0.0   
429          False               sqrt                              0.5   
430          False               sqrt                              0.5   
431          False               sqrt                              0.5   

    convert_categorical  
0               numeric  
1      simplified_dummy  
2                 dummy  
3               numeric  
4      simplified_dummy  
..                  ...  
427    simplified_dummy  
428               dummy  
429             numeric  
430    simplified_dummy  
431               dummy  

[432 rows x 7 columns]

Then we need to create a cleaned/pre-processed version of the training and validation datasets for each combination of these judgment calls:

In [46]:
# conduct judgment call perturbations of training data
ames_jc_perturb = [preprocess_ames_data(ames_train_clean,
                                        max_identical_thresh=perturb_options['max_identical_thresh'][i],
                                        n_neighborhoods=perturb_options['n_neighborhoods'][i],
                                        impute_missing_categorical=perturb_options['impute_missing_categorical'][i],
                                        simplify_vars=perturb_options['simplify_vars'][i],
                                        transform_response=perturb_options['transform_response'][i],
                                        cor_feature_selection_threshold=perturb_options['cor_feature_selection_threshold'][i],
                                        convert_categorical=perturb_options['convert_categorical'][i])
                   for i in range(perturb_options.shape[0])]

# conduct judgment call perturbations of validation data data (we need to make sure each validation set is compartible with the relevant training set)
ames_val_jc_perturb = []
for i in range(perturb_options.shape[0]):
    
    # extract relevant neighborhoods from  relevant training data
    train_neighborhood_cols = list(ames_jc_perturb[i].filter(regex="neighborhood").columns)
    train_neighborhoods = [x.replace("neighborhood_", "") for x in train_neighborhood_cols]
    
    # create preprocessed validation set
    ames_val_jc_perturb.append(
        preprocess_ames_data(ames_val_clean,
                             max_identical_thresh=perturb_options['max_identical_thresh'][i],
                             n_neighborhoods=perturb_options['n_neighborhoods'][i],
                             impute_missing_categorical=perturb_options['impute_missing_categorical'][i],
                             simplify_vars=perturb_options['simplify_vars'][i],
                             transform_response=perturb_options['transform_response'][i],
                             cor_feature_selection_threshold=perturb_options['cor_feature_selection_threshold'][i],
                             convert_categorical=perturb_options['convert_categorical'][i],
                             # make sure val set matches training set
                             column_selection=list(ames_jc_perturb[i].columns),
                             neighborhood_levels=train_neighborhoods)
        )

# create a standardized version of the validation datasets
ames_val_jc_perturb_std = []
for i in range(len(ames_val_jc_perturb)):
    df = ames_val_jc_perturb[i].drop(columns=['saleprice'])
    df_std = (df - df.mean()) / df.std()
    df_std['saleprice'] = ames_val_jc_perturb[i]['saleprice']
    ames_val_jc_perturb_std.append(df_std)

Then we can essentially repeat the code from above, but for these judgment call-perturbed datasets. However, since the judgment calls primarily don't affect the single-predictor and 5-predictor fits, we will just focus on the LS (all predictor) fit and the lasso and ridge regularized fits.

In [47]:
# compute the fits for each perturbed dataset
# Note some of the fits don't converge but for simplicity we will ignore this for now
results_jc = Parallel(n_jobs=-1)(delayed(fit_models)(df, fit_area_multi=False) for df in ames_jc_perturb)
ls_all_jc_perturbed, ridge_jc_perturbed, lasso_jc_perturbed = zip(*results_jc)

/Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/site-packages/sklearn/linear_model/_coordinate_descent.py:628: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 1.766e+11, tolerance: 4.522e+08
  model = cd_fast.enet_coordinate_descent(
/Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/site-packages/sklearn/linear_model/_coordinate_descent.py:628: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 2.090e+11, tolerance: 5.257e+08
  model = cd_fast.enet_coordinate_descent(
/Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/site-packages/sklearn/linear_model/_coordinate_descent.py:628: ConvergenceWarning: Objective did not converge. You might want to increase the number of iter

In [48]:
# compute the predictions on the validaion set for ls_area_perturbed, ls_multi_perturbed, ls_all_perturbed, ridge_perturbed, and lasso_perturbed
ls_all_val_jc_pred_perturbed = [ls_all_jc_perturbed[i].predict(X=ames_val_jc_perturb[i].drop(columns='saleprice')) for i in range(len(ames_val_jc_perturb))]
ridge_val_jc_pred_perturbed = [ridge_jc_perturbed[i].predict(X=ames_val_jc_perturb_std[i].drop(columns='saleprice')) for i in range(len(ames_val_jc_perturb_std))]
lasso_val_jc_pred_perturbed = [lasso_jc_perturbed[i].predict(X=ames_val_jc_perturb_std[i].drop(columns='saleprice')) for i in range(len(ames_val_jc_perturb_std))]

# for predictions where the response was log-transformed, undo the log transformation
ls_all_val_jc_pred_perturbed = [np.exp(pred) if perturb_options['transform_response'][i] == 'log' else pred for i, pred in enumerate(ls_all_val_jc_pred_perturbed)]
ridge_val_jc_pred_perturbed = [np.exp(pred) if perturb_options['transform_response'][i] == 'log' else pred for i, pred in enumerate(ridge_val_jc_pred_perturbed)]
lasso_val_jc_pred_perturbed = [np.exp(pred) if perturb_options['transform_response'][i] == 'log' else pred for i, pred in enumerate(lasso_val_jc_pred_perturbed)]

# for predictions where the response was sqrt-transformed, undo the sqrt transformation
ls_all_val_jc_pred_perturbed = [pred**2 if perturb_options['transform_response'][i] == 'sqrt' else pred for i, pred in enumerate(ls_all_val_jc_pred_perturbed)]
ridge_val_jc_pred_perturbed = [pred**2 if perturb_options['transform_response'][i] == 'sqrt' else pred for i, pred in enumerate(ridge_val_jc_pred_perturbed)]
lasso_val_jc_pred_perturbed = [pred**2 if perturb_options['transform_response'][i] == 'sqrt' else pred for i, pred in enumerate(lasso_val_jc_pred_perturbed)]


We next want to use it to visualize the range of perturbed predictions for 150 validation set houses for each fit. However, first, we should filter any particularly poorly performing fits. To identify whether there are any particularly poorly performing fits, let's compute the correlation predictive performance for each fit to each perturbed dataset and visualize their distributions across the different fits and judgment calls.

In [49]:
# compute the correlation between the predictions and the true values for each model
# note that we are using the sale price from the unperturbed validation set because to use the perturbed sale price
# we would need to un log- or sqrt-transform the sale price where relevant
# this wouldn't work if any of our judgment call modifications changed the *number* of observations in the data
ls_all_val_jc_corr = [np.corrcoef(ames_val_preprocessed['saleprice'], pred)[0, 1] for pred in ls_all_val_jc_pred_perturbed]
ridge_val_jc_corr = [np.corrcoef(ames_val_preprocessed['saleprice'], pred)[0, 1] for pred in ridge_val_jc_pred_perturbed]
lasso_val_jc_corr = [np.corrcoef(ames_val_preprocessed['saleprice'], pred)[0, 1] for pred in lasso_val_jc_pred_perturbed]

Let's visualize these correlations against each of the judgment call options for each fit:


In [50]:
# Create a boxplot of the correlations for each fit against each judgment call combination
corr_df = pd.DataFrame({'ls_all': ls_all_val_jc_corr,
                        'ridge': ridge_val_jc_corr,
                        'lasso': lasso_val_jc_corr,
                        'max_identical_thresh': perturb_options['max_identical_thresh'],
                        'n_neighborhoods': perturb_options['n_neighborhoods'],
                        'impute_missing_categorical': perturb_options['impute_missing_categorical'],
                        'simplify_vars': perturb_options['simplify_vars'],
                        'transform_response': perturb_options['transform_response'],
                        'cor_feature_selection_threshold': perturb_options['cor_feature_selection_threshold'],
                        'convert_categorical': perturb_options['convert_categorical']})

# melt corr_df by the model
corr_df = pd.melt(corr_df, id_vars=['max_identical_thresh', 
                                    'n_neighborhoods',
                                    'impute_missing_categorical',
                                    'simplify_vars',
                                    'transform_response',
                                    'cor_feature_selection_threshold',
                                    'convert_categorical'],
                  value_vars=['ls_all', 'ridge', 'lasso'],
                  var_name='model',
                  value_name='corr')

corr_df.sort_values(by='corr', ascending=False)

max_identical_thresh  n_neighborhoods impute_missing_categorical  \
427                   0.95               20                       mode   
426                   0.95               20                       mode   
391                   0.95               20                      other   
390                   0.95               20                      other   
385                   0.95               20                      other   
...                    ...              ...                        ...   
1211                  0.95               10                       mode   
1175                  0.95               10                      other   
1031                  0.80               10                      other   
887                   0.65               10                      other   
1067                  0.80               10                       mode   

      simplify_vars transform_response  cor_feature_selection_threshold  \
427           False               sqrt                              0.0   
426           False               sqrt                              0.0   
391           False               sqrt                              0.0   
390           False               sqrt                              0.0   
385           False                log                              0.0   
...             ...                ...                              ...   
1211          False               none                              0.5   
1175          False               none                              0.5   
1031          False               none                              0.5   
887           False               none                              0.5   
1067          False               none                              0.5   

     convert_categorical   model      corr  
427     simplified_dummy  ls_all  0.968213  
426              numeric  ls_all  0.968187  
391     simplified_dummy  ls_all  0.968153  
390              numeric  ls_all  0.967781  
385     simplified_dummy  ls_all  0.967483  
...                  ...     ...       ...  
1211               dummy   lasso  0.894414  
1175               dummy   lasso  0.894414  
1031               dummy   lasso  0.894414  
887                dummy   lasso  0.894414  
1067               dummy   lasso  0.894414  

[1296 rows x 9 columns]

In [51]:
corr_df_long = corr_df.melt(id_vars=['corr', 'model'],
                            value_vars=['max_identical_thresh',
                                        'n_neighborhoods',
                                        'impute_missing_categorical',
                                        'simplify_vars',
                                        'transform_response',
                                        'cor_feature_selection_threshold',
                                        'convert_categorical'],
                            var_name='judgment_call',
                            value_name='option')
fig = px.box(corr_df_long, x='option', y='corr', 
       color='model', 
       facet_col='judgment_call', 
       facet_col_wrap=2, 
       height=1200)

# give each plot in the 4 by 2 fig above its own x-axis
fig.update_xaxes(matches=None, showticklabels=True)
fig.update_yaxes(matches=None)


The main takeaway is that transforming the response dramatically improves the predictive performance, and applying correlation feature selection dramatically diminishes it. Based on this figure, **let's use a predictability screening test that requires each fit has at least a validation set correlation performance of 0.93**. 

Note that this implementation of lasso performs worse than the version we implemented in R, but it has better stability, as you will see below. You could probably tweak the lasso analysis (e.g., by tweaking the range of the alpha parameter, etc) so that it performs better (likely at the cost of the stability performance), but we will leave that as an exercise for the reader.

In [52]:
# identify which models pass the predictability screening for each fit. Extract integer positions for each model
ls_all_screen_index = corr_df_long.query('model=="ls_all"').reset_index().query('corr >= 0.93').index
ridge_screen_index = corr_df_long.query('model=="ridge"').reset_index().query('corr >= 0.93').index
lasso_screen_index = corr_df_long.query('model=="lasso"').reset_index().query('corr >= 0.93').index

In [53]:
# extract just the perturbed predictions that pass the screening
ls_all_val_pred_perturbed_screened = [x for i, x in enumerate(ls_all_val_jc_pred_perturbed) if i in ls_all_screen_index]
plot_prediction_range(ls_all_val_pred_perturbed_screened, 'LS (all)', sample_index=val_sample_id)

In [54]:
# extract just the perturbed predictions that pass the screening
ridge_val_pred_perturbed_screened = [x for i, x in enumerate(ridge_val_jc_pred_perturbed) if i in ridge_screen_index]
plot_prediction_range(ridge_val_pred_perturbed_screened, 'Ridge (1SE)', sample_index=val_sample_id)

In [55]:
# extract just the perturbed predictions that pass the screening
lasso_val_pred_perturbed_screened = [x for i, x in enumerate(lasso_val_jc_pred_perturbed) if i in lasso_screen_index]
plot_prediction_range(lasso_val_pred_perturbed, 'Lasso (1SE)', sample_index=val_sample_id)


The three plots look fairly similar, but we can compute the average SD of the observation-specific predictions for each fit (that passed the predictability screening) to compare.

In [56]:
print(f"LS (all) average sd: {pd.DataFrame(ls_all_val_pred_perturbed_screened).std(axis=0).mean()}")
print(f"Ridge (1SE) average sd: {pd.DataFrame(ridge_val_pred_perturbed_screened).std(axis=0).mean()}")
print(f"Lasso (1SE) average sd: {pd.DataFrame(lasso_val_pred_perturbed_screened).std(axis=0).mean()}")

LS (all) average sd: 8658.273309405626
Ridge (1SE) average sd: 7173.476132101139
Lasso (1SE) average sd: 4083.2369835840877



From the table above, it again seems that the regularization helps improve the stability of the predictions to judgment call perturbations, since the average observation-specific SD of the predictions are smaller for the `lasso` and `ridge` fits than for the unregularized (`ls_all`) fit.


Lastly, we will again look at the stability of the coefficients themselves.

Again, to ensure that the ridge/lasso coefficients are comparable with the unregularized coefficients, we will re-fit each of the unregularized fits using the standardized data.

In [57]:
# create perturbations of the standardized dataset
perturbed_ames_jc_std = [(df - df.mean()) / df.std() for df in ames_jc_perturb]

# refit all of the fits using the standardized JC perturbed datasets
results_jc_std = Parallel(n_jobs=-1)(delayed(fit_models)(df, reg=True, fit_area_multi=False) for df in perturbed_ames_jc_std)
ls_all_jc_perturbed_std, ridge_jc_perturbed_std, lasso_jc_perturbed_std = zip(*results_jc_std)


# extract coefficients for all models
perturbed_jc_std_coefs_ls_all = extract_coefficients(ls_all_jc_perturbed_std, 'ls_all')
perturbed_jc_std_coefs_ridge = extract_coefficients(ridge_jc_perturbed_std, 'ridge')
perturbed_jc_std_coefs_lasso = extract_coefficients(lasso_jc_perturbed_std, 'lasso')

In [58]:
# concatenate the dataframes
perturbed_jc_std_coefs_combined = pd.concat([perturbed_jc_std_coefs_ls_all, 
                                     perturbed_jc_std_coefs_ridge, 
                                     perturbed_jc_std_coefs_lasso])



# identify the 20 variables with the largest coefficients in the LS (all) model
top_20_coefs_jc_ls_all = perturbed_jc_std_coefs_ls_all.groupby('variable') \
    .agg({'coef': 'mean'}) \
    .sort_values(by='coef', ascending=False) \
    .head(20) \
    .index
top_20_coefs_jc_ls_all


Index(['gr_liv_area', 'overall_qual', '2nd_flr_sf', 'total_bsmt_sf',
       'overall_cond', 'bsmtfin_sf_1', 'year_built', '1st_flr_sf',
       'garage_area', 'bathrooms', 'lot_frontage', 'fireplaces',
       'kitchen_qual', 'bsmt_exposure', 'neighborhood_NoRidge', 'mas_vnr_area',
       'lot_area', 'neighborhood_NridgHt', 'neighborhood_Crawfor',
       'foundation_concrete'],
      dtype='object', name='variable')


Then we can create a series of boxplots showing the distribution of each perturbed coefficient for each fit


In [59]:

# extract the coefficients for the top 20 variables from perturbed_std_coefs_combined and visualize their distributions using boxplots
top_20_coefs_jc_df = perturbed_jc_std_coefs_combined.query('variable in @top_20_coefs_jc_ls_all')

fig = px.box(top_20_coefs_jc_df,
             x='variable',
             y='coef',
             facet_col='model',
             facet_col_wrap=1,
             height=1200,
             category_orders={'variable': top_20_coefs_jc_ls_all})
fig.update_traces(width=0.5)
fig
